Minimal test to diagnose VedEf model issues.


In [ ]:
import importlib.util
import traceback
from pathlib import Path

# Import setup_vedef_problem from the numbered file
spec = importlib.util.spec_from_file_location(
    "problem_module", Path(__file__).parent / "1_setup_vedef_problem.py"
)
problem_module = importlib.util.module_from_spec(spec)
spec.loader.exec_module(problem_module)
setup_vedef_problem = problem_module.setup_vedef_problem

# Test parameters (nominal values)
V = 20000.0  # 20 kV
e = 0.01  # 10 mm
d_t = 0.02  # 20 mm
f = 50000.0  # 50 kHz
E_p = 0.010  # 10 mJ

print("Creating problem...")
try:
    prob = setup_vedef_problem()
    print("Setup successful!")
except Exception as e:
    print(f"Setup failed: {e}")
    traceback.print_exc()
    exit(1)

print("\nSetting parameters...")
try:
    # Set fixed parameters
    prob.set_val("pulse_duration", 1e-6, units="s")
    prob.set_val("TP_QM", 160.0 / 86400.0, units="kg/s")  # Mass flow

    # Set design variables (using ARC002 parameter tags)
    prob.set_val("G_UMAX_OUT", V, units="V")  # HV voltage
    prob.set_val("G_e", e, units="m")  # Gap distance
    prob.set_val("TP_D_OUT", d_t, units="m")  # Torch diameter
    prob.set_val("G_F", f, units="Hz")  # Pulse frequency
    prob.set_val("G_Ep", E_p, units="J")  # Energy per pulse
    print("Parameters set successfully!")
except Exception as e:
    print(f"Parameter setting failed: {e}")
    traceback.print_exc()
    exit(1)

print("\nRunning model...")
try:
    prob.run_model()
    print("Model run successful!")
except Exception as e:
    print(f"Model run failed: {e}")
    traceback.print_exc()
    exit(1)

print("\nExtracting results...")
try:
    print(f"T_0 = {prob.get_val('T_0', units='K')[0]:.1f} K")
    print(f"T_max = {prob.get_val('T_max', units='K')[0]:.1f} K")
    print(f"Breakdown voltage = {prob.get_val('breakdown_voltage', units='V')[0] / 1e3:.1f} kV")
    print(f"Breakdown margin = {prob.get_val('breakdown_margin', units='V')[0] / 1e3:.1f} kV")
    print(f"Coverage fraction = {prob.get_val('coverage_fraction')[0]:.3f}")
    print(f"Coverage margin = {prob.get_val('coverage_margin')[0]:.3f}")
    print(f"Energy density = {prob.get_val('energy_density', units='J/m**3')[0] / 1e6:.1f} MJ/m3")
    print(f"Density margin = {prob.get_val('density_margin', units='J/m**3')[0] / 1e6:.1f} MJ/m3")
    print(f"Flow velocity = {prob.get_val('flow_velocity', units='m/s')[0]:.2f} m/s")
    print(f"Residence time = {prob.get_val('residence_time', units='s')[0] * 1e3:.2f} ms")
    print(f"Operating window power = {prob.get_val('operating_window_power', units='W')[0]:.1f} W")
    print(f"Power error = {prob.get_val('PowerConstraint.power_error')[0] * 100:.1f}%")

    print("\nAll results extracted successfully!")
except Exception as e:
    print(f"Result extraction failed: {e}")
    traceback.print_exc()
    exit(1)